In [22]:
!pip install datasets
!pip install streamlit
!pip install transformers
!pip install tqdm

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [27]:
from datasets import load_dataset
import pandas as pd
import numpy as np
import os
import json
import torch
import sys
from tqdm import tqdm

import streamlit as st
from transformers import TextClassificationPipeline, pipeline
from transformers import AutoTokenizer, AutoModelForSequenceClassification, DistilBertTokenizerFast, DistilBertForSequenceClassification

In [3]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [39]:
abstract_model = TextClassificationPipeline(
  model = DistilBertForSequenceClassification.from_pretrained('rk2546/uspto-patents-abstracts'),
  tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased'),
  padding = True, 
  truncation = True,
  return_all_scores = True
)

claim_model = TextClassificationPipeline(
  model = DistilBertForSequenceClassification.from_pretrained('rk2546/uspto-patents-claims'),
  tokenizer = DistilBertTokenizerFast.from_pretrained('distilbert-base-uncased'),
  padding = True, 
  truncation = True,
  return_all_scores = True
)

/usr/local/lib/python3.9/dist-packages/transformers/pipelines/text_classification.py:104: UserWarning: `return_all_scores` is now deprecated,  if want a similar funcionality use `top_k=None` instead of `return_all_scores=True` or `top_k=1` instead of `return_all_scores=False`.
  warnings.warn(


In [7]:
path_to_valData = "./gdrive/MyDrive/AI [Spring 2023]/cs-gy-6613-project-rk2546/val.json"
f = open(path_to_valData)
valData = json.load(f)
f.close()

In [48]:
# We track the successes of abstracts, claims, and both combined
abstract_successes = 0
claim_successes = 0
aggregate_successes = 0
total_num = len(valData['labels'])

# By default, we weigh the claims more highly than abstracts
claim_weight = 0.5
abstract_weight = 0.5

# To randomize the data, we generate random indices 
index_perms = np.random.permutation(total_num)
labels = []
abstracts = []
claims = []
# We generate up to 500 samples to validate against
new_total_num = min(1000,len(index_perms))
for i in range(new_total_num):
  labels.append(valData['labels'][index_perms[i]])
  abstracts.append(valData['abstracts'][index_perms[i]])
  claims.append(valData['claims'][index_perms[i]])

# Now we validate
for i in tqdm(range(new_total_num)):
  label = labels[i]
  abstract = abstracts[i]
  claim = claims[i]

  abstract_response = abstract_model(abstract)[0]
  claim_response = claim_model(claim)[0]
  aggregate_response = [
    {'label':'REJECTED','score':abstract_response[0]['score']*abstract_weight + claim_response[0]['score']*claim_weight},
    {'label':'ACCEPTED','score':abstract_response[1]['score']*abstract_weight + claim_response[1]['score']*claim_weight}
  ]

  abstract_sorted = sorted(abstract_response, key=lambda d: d['score'], reverse=True) 
  claim_sorted = sorted(claim_response, key=lambda d: d['score'], reverse=True)
  aggregate_sorted = sorted(aggregate_response, key=lambda d: d['score'], reverse=True) 

  if abstract_sorted[0]['label'] == 'LABEL_1' and label == 1:
    abstract_successes += 1
  elif abstract_sorted[0]['label'] == 'LABEL_0' and label == 0:
    abstract_successes += 1
  
  if claim_sorted[0]['label'] == 'LABEL_1' and label == 1:
    claim_successes += 1
  elif claim_sorted[0]['label'] == 'LABEL_0' and label == 0:
    claim_successes += 1
  
  if aggregate_sorted[0]['label'] == 'ACCEPTED' and label == 1:
    aggregate_successes += 1
  elif aggregate_sorted[0]['label'] == 'REJECTED' and label == 0:
    aggregate_successes += 1

  # At 10% intervals, we print the current results
  if i > 0 and i % (new_total_num * 0.1) == 0:
    print(f"\nAbs: {abstract_successes}/{i} | Cl: {claim_successes}/{i} | Agg: {aggregate_successes}/{i}")

# Calculate final accuracy
abstract_accuracy = abstract_successes / new_total_num
claim_accuracy = claim_successes / new_total_num
aggregate_accuracy = aggregate_successes / new_total_num

# Display accuracy
print("\n")
print(f"Abstract Model Accuracy: {abstract_accuracy * 100}%")
print(f"Claim Model Accuracy: {claim_accuracy * 100}%")
print(f"Aggregated Model Accuracy: {aggregate_accuracy * 100}%")

 10%|█         | 101/1000 [02:25<22:03,  1.47s/it]


Abs: 70/100 | Cl: 73/100 | Agg: 73/100


 20%|██        | 201/1000 [04:38<21:25,  1.61s/it]


Abs: 148/200 | Cl: 155/200 | Agg: 155/200


 30%|███       | 301/1000 [06:53<13:59,  1.20s/it]

...


Abs: 601/800 | Cl: 591/800 | Agg: 626/800


 90%|█████████ | 901/1000 [20:24<01:56,  1.18s/it]


Abs: 670/900 | Cl: 666/900 | Agg: 703/900


100%|██████████| 1000/1000 [22:36<00:00,  1.36s/it]



Abstract Model Accuracy: 72.89999999999999%
Claim Model Accuracy: 72.8%
Aggregated Model Accuracy: 76.2%
